In [1]:
if 'google.colab' in str(get_ipython()):
  from google.colab import drive
  drive.mount('/content/drive')

In [17]:
!pip install pypdf --quiet
!pip install tiktoken --quiet

In [5]:
import os
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.chat_models import ChatOpenAI
from langchain.chains import ConversationalRetrievalChain
from langchain.document_loaders.csv_loader import CSVLoader
from langchain_community.document_loaders import PyPDFLoader
from langchain.vectorstores import FAISS
from langchain.prompts import load_prompt
# from langchain_text_splitters.base import TextSplitter
# from pymongo import MongoClient
# from pymongo.mongo_client import MongoClient
# from pymongo.server_api import ServerApi
import json
import time
import datetime
import pypdf

In [3]:
# from pathlib import Path
# path = Path("/content/drive/MyDrive/Colab_Notebooks/resume-bot")

In [6]:
prompt_template = "templates/template.json"
faiss_index = "faiss_index"
data_source = "data/about_hari.csv"
pdf_source = "data/HarikrishnaDev_DataScientist.pdf"

In [7]:
pdf_source

'data/HarikrishnaDev_DataScientist.pdf'

In [8]:
def is_valid_json(data):
    try:
        json.loads(data)
        return True
    except json.JSONDecodeError:
        return False

In [9]:
import os
os.environ['OPENAI_API_KEY'] = "#Enter OpenAI Key"

In [10]:
embeddings = OpenAIEmbeddings()

/Users/harikrishnadev/.pyenv/versions/3.11.8/lib/python3.11/site-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `OpenAIEmbeddings` was deprecated in LangChain 0.0.9 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAIEmbeddings`.
  warn_deprecated(


In [11]:
from langchain.text_splitter import CharacterTextSplitter
text_splitter = CharacterTextSplitter(
    separator="\n",
    chunk_size=400,
    chunk_overlap=40
)

In [12]:
pdf_loader = PyPDFLoader(pdf_source)
pdf_data = pdf_loader.load_and_split(text_splitter=text_splitter)

In [13]:
pdf_data

[Document(page_content='Harikrishna (Harry) Dev  \nharikrish0607@gmail.com ; +1 (425) 469 -2587 ; Dallas, TX (Open to relocation)  \nlinkedin.com/in/harikrishnad1997 ; harikrishnad1997.github.io ; github.com/harikrishnad1997 ; Resume LLM  \n \nPROFESSIONAL  EXPERIENCE  \nDaifuku Holding Pvt Ltd , Novi, MI  May 2023  – August 2023  \nIT Analyst Intern – Data Science', metadata={'source': 'data/HarikrishnaDev_DataScientist.pdf', 'page': 0}),
 Document(page_content='IT Analyst Intern – Data Science  \n• Developed  proprietary Generative AI  (GenAI)  tool to perform text mining on report documents and  provide \nsource citations by leveraging the HuggingFace  and Large Language models , reducing  2 hours daily  work  for Legal  \n• Augmented  the Paint Line assembly efficiency by 48% by identifying bottlenecks and forecasting recurring issues', metadata={'source': 'data/HarikrishnaDev_DataScientist.pdf', 'page': 0}),
 Document(page_content='in the assembly line using Regularized Linear mod

In [14]:
csv_loader = CSVLoader(file_path=data_source, encoding="utf-8")
csv_data = csv_loader.load()

In [15]:
csv_data

[Document(page_content='question: what is his educational background| tell me about his education| where did he go to school\nanswer: Harikrishna (Harry) Dev holds a Master of Sciences in Business Analytics - Data Science cohort at The University of Texas at Dallas and a Bachelor of Technology in Mechanical Engineering from National Institute of Technology Karnataka, India (graduated May 2019) , where he has taken leadership roles as a Graduate Student Assistant and Technical Officer of the Data Science Club.', metadata={'source': 'data/about_hari.csv', 'row': 0}),
 Document(page_content='question: does he have any certificates? what kind of certificate he has?\nanswer: Harikrishna Dev has certifications and training in the following: Python Data Structures, Hadoop in Real World, IBM: Data Science Methodology He also has hand on experience with AWS, GCP, Azure, Databricks, and Snowflake', metadata={'source': 'data/about_hari.csv', 'row': 1}),
 Document(page_content="question: How can I

In [18]:
# Combine PDF and CSV data
data = pdf_data + csv_data

# Create embeddings for the docs
vectors = FAISS.from_documents(data, embeddings)
vectors.save_local("faiss_index")

In [19]:
openai_api_key = os.getenv("OPENAI_API_KEY")

In [20]:
prompt = load_prompt("templates/template.json")

In [21]:
retriever = vectors.as_retriever(search_type="similarity", search_kwargs={"k":6, "include_metadata":True, "score_threshold":0.6})
chain = ConversationalRetrievalChain.from_llm(llm=ChatOpenAI(temperature=0.5,model_name='gpt-3.5-turbo', openai_api_key=openai_api_key), 
                                                retriever=retriever,return_source_documents=True,verbose=True,chain_type="stuff",
                                                max_tokens_limit=4097, combine_docs_chain_kwargs={"prompt": prompt})


/Users/harikrishnadev/.pyenv/versions/3.11.8/lib/python3.11/site-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `ChatOpenAI` was deprecated in LangChain 0.0.10 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import ChatOpenAI`.
  warn_deprecated(


In [23]:
chat_history = []
result = chain({"system": 
        "You are a Resume Bot, a comprehensive, interactive resource for exploring Harikrishna (Harry) Dev's background, skills, and expertise. Be polite and provide answers based on the provided context only. Use only the provided data and not prior knowledge.", 
                        "question": "Where did Hari study?",
                        "chat_history":chat_history})



> Entering new StuffDocumentsChain chain...


> Entering new LLMChain chain...
Prompt after formatting:
System: You are a Resume Bot, a comprehensive, interactive resource for exploring Harikrishna (Harry) Dev's background, skills, and expertise. Be polite and provide answers based on the provided context only. Use only the provided data and not prior knowledge. 
 Human: Take a deep breath and do the following step by step these 4 steps:  
 1. Read the context below 
 2. Answer the question with detail using the provided Help Centre information 
 3. Make sure to nicely format the output is a three paragraph answer and try to incorporate the STAR format. 
 4. Provide 3 examples of questions user can ask about Harikrishna Dev based on the questions from context. Context : 
 ~~~ question: what languages does Hari speak
answer: Hari speaks English, Hindi, Tamil, Kannada and Tulu.

question: Where is he based out of? | Where does he live? | Where is he located? | Where is Hari?
answer: Ha

In [24]:
result

{'system': "You are a Resume Bot, a comprehensive, interactive resource for exploring Harikrishna (Harry) Dev's background, skills, and expertise. Be polite and provide answers based on the provided context only. Use only the provided data and not prior knowledge.",
 'question': 'Where did Hari study?',
 'chat_history': [],
 'answer': '{\n    "answered": true,\n    "response": "Harikrishna Dev completed his Bachelor of Technology in Mechanical Engineering from National Institute of Technology Karnataka, India in May 2019. He then pursued his Master of Sciences in Business Analytics - Data Science at The University of Texas at Dallas, graduating in May 2024.",\n    "questions": [\n        "What degrees does Hari hold?",\n        "Where did Hari complete his Bachelor\'s degree?",\n        "What universities did Hari attend for his education?"\n    ]\n}',
 'source_documents': [Document(page_content='question: what languages does Hari speak\nanswer: Hari speaks English, Hindi, Tamil, Kanna

In [25]:
result['answer']

'{\n    "answered": true,\n    "response": "Harikrishna Dev completed his Bachelor of Technology in Mechanical Engineering from National Institute of Technology Karnataka, India in May 2019. He then pursued his Master of Sciences in Business Analytics - Data Science at The University of Texas at Dallas, graduating in May 2024.",\n    "questions": [\n        "What degrees does Hari hold?",\n        "Where did Hari complete his Bachelor\'s degree?",\n        "What universities did Hari attend for his education?"\n    ]\n}'

In [26]:
data = json.loads(result["answer"])

In [27]:
data.get("response")

'Harikrishna Dev completed his Bachelor of Technology in Mechanical Engineering from National Institute of Technology Karnataka, India in May 2019. He then pursued his Master of Sciences in Business Analytics - Data Science at The University of Texas at Dallas, graduating in May 2024.'

In [28]:
data.get("questions")

['What degrees does Hari hold?',
 "Where did Hari complete his Bachelor's degree?",
 'What universities did Hari attend for his education?']

In [102]:
chat_history.append((result["question"], result["answer"]))

In [103]:
chat_history

[('Has Hari worked on GenAI?',
  '{\n  "answered": true,\n  "response": "Yes, Harikrishna has worked on GenAI. His favorite project is the GenAI application he developed during his internship at Daifuku. This project involved building an AI-powered tool to support the legal team in managing compliance documentation, which decreased 2 hours of daily grunt work.",\n  "questions": [\n    "What was Harikrishna\'s favorite project?",\n    "Can you provide more details about the GenAI application Harikrishna worked on?",\n    "How did GenAI impact the daily workflow at Daifuku?"\n  ]\n}')]

In [104]:
result = chain({"system": 
        "You are a Resume Bot, a comprehensive, interactive resource for exploring Harikrishna (Harry) Dev's background, skills, and expertise. Be polite and provide answers based on the provided context only. Use only the provided data and not prior knowledge.", 
                        "question": "Can you provide more details about the GenAI application Harikrishna worked on?",
                        "chat_history":chat_history})



> Entering new LLMChain chain...
Prompt after formatting:
Given the following conversation and a follow up question, rephrase the follow up question to be a standalone question, in its original language.

Chat History:

Human: Has Hari worked on GenAI?
Assistant: {
  "answered": true,
  "response": "Yes, Harikrishna has worked on GenAI. His favorite project is the GenAI application he developed during his internship at Daifuku. This project involved building an AI-powered tool to support the legal team in managing compliance documentation, which decreased 2 hours of daily grunt work.",
  "questions": [
    "What was Harikrishna's favorite project?",
    "Can you provide more details about the GenAI application Harikrishna worked on?",
    "How did GenAI impact the daily workflow at Daifuku?"
  ]
}
Follow Up Input: Can you provide more details about the GenAI application Harikrishna worked on?
Standalone question:

> Finished chain.


> Entering new StuffDocumentsChain chain...


> En

In [105]:
result["answer"]

'{\n    "answered": true,\n    "response": "Harikrishna\'s favorite project is the GenAI application he developed during his internship at Daifuku. This project involved building an AI-powered tool to support the legal team in managing compliance documentation, which decreased 2 hours of daily grunt work. The GenAI application utilized Natural Language Processing and the HuggingFace API for text mining reports, demonstrating Harikrishna\'s expertise in AI and machine learning applications in real-world scenarios.",\n    "questions": [\n        "What technologies did Harikrishna use in developing the GenAI application?",\n        "How did the GenAI application impact the daily workflow at Daifuku?",\n        "Can you provide more details about the specific features of the GenAI application?"\n    ]\n}'

In [106]:
chat_history.append((result["question"], result["answer"]))

In [107]:
result = chain({"system": 
        "You are a Resume Bot, a comprehensive, interactive resource for exploring Harikrishna (Harry) Dev's background, skills, and expertise. Be polite and provide answers based on the provided context only. Use only the provided data and not prior knowledge.", 
                        "question": "Does he know Snowflake?",
                        "chat_history":chat_history})



> Entering new LLMChain chain...
Prompt after formatting:
Given the following conversation and a follow up question, rephrase the follow up question to be a standalone question, in its original language.

Chat History:

Human: Has Hari worked on GenAI?
Assistant: {
  "answered": true,
  "response": "Yes, Harikrishna has worked on GenAI. His favorite project is the GenAI application he developed during his internship at Daifuku. This project involved building an AI-powered tool to support the legal team in managing compliance documentation, which decreased 2 hours of daily grunt work.",
  "questions": [
    "What was Harikrishna's favorite project?",
    "Can you provide more details about the GenAI application Harikrishna worked on?",
    "How did GenAI impact the daily workflow at Daifuku?"
  ]
}
Human: Can you provide more details about the GenAI application Harikrishna worked on?
Assistant: {
    "answered": true,
    "response": "Harikrishna's favorite project is the GenAI applic

In [108]:
result["answer"]

'{\n    "answered": true,\n    "response": "Yes, Harikrishna has experience with Snowflake. He utilized Snowflake during his time at Walmart to train and deploy machine learning models and manage big data warehouses. His proficiency with Snowflake contributed to the success of projects involving data analytics and machine learning.",\n    "questions": [\n        "What projects has Harikrishna worked on using Snowflake?",\n        "How did Harikrishna leverage Snowflake in his machine learning projects?",\n        "Can Harikrishna provide examples of the impact of using Snowflake in data warehouse management?"\n    ]\n}'